In [ ]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

In [ ]:

from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
!pip install neuralprophet
!pip install git+https://github.com/ourownstory/neural_prophet.git numpy==1.23.5

  Cloning https://github.com/ourownstory/neural_prophet.git to /tmp/pip-req-build-wvspds1v
  Running command git clone --filter=blob:none --quiet https://github.com/ourownstory/neural_prophet.git /tmp/pip-req-build-wvspds1v
  Resolved https://github.com/ourownstory/neural_prophet.git to commit 23543560b4ed278e84d1fd0f119d332342336d0d
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Using cached numpy-1.23.5-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (17.1 MB)
  Using cached kaleido-0.2.1-py2.py3-none-manylinux1_x86_64.whl (79.9 MB)
INFO: pip is looking at multiple versions of neuralprophet to determine which version is compatible with other requirements. This could take a while.
ERROR: Cannot install neuralprophet==1.0.0rc10 and numpy==1.23.5 because these package versions have conflicting dependencies.

The conflict is caused by:
    The user requested numpy==1.23.5
    neuralprophe

In [ ]:
from neuralprophet import NeuralProphet
import datetime
from sklearn.metrics import mean_absolute_error, mean_squared_error

### Data detail

$ I_{\text{vsc}} $ (1 hour): vc_weather_data.csv
March 9, 2023 - February 29, 2024

$ I_{\text{ncep}} $ (15 minutes) siteCU03_xxx.csv
January 1, 2023 - January 1, 2024

$ I_{\text{actual}} $ (1 minute) EE_station 1_xxx.csv
January 1, 2023 - December 31, 2023

$ \text{CI} $ (10 minute)
January 1, 2023 - December 31, 2023

$ \text{PV}_{\text{actual}} $ (5 minutes, 15 minutes)  pv_data_5min_xxx.csv
March 9, 2023 - February 29, 2024

In [ ]:
pip install --upgrade pandas

### Incep => ncep_df

In [ ]:
def read_ncep_data(filename):
    _df = pd.read_csv(filename,sep=";", skiprows=26, names=col_names)
    _df['Time'] = _df['Time'].replace("24:00", "00:00")

    # Concatenate Date and Time columns
    _df['Datetime'] = _df['Date'] + " " + _df['Time']

    # Convert to datetime type
    _df['Datetime'] = pd.to_datetime(_df['Datetime'])

    # Identify rows where 'Time' is "00:00" and adjust the 'Date' by adding 1 day

    next_day_mask = _df['Time'] == "00:00"
    _df.loc[next_day_mask, 'Datetime'] += pd.DateOffset(days=1)
    _df['Datetime'] = _df['Datetime'] + pd.DateOffset(hours=7)

    dropped_cols = ['Date', 'Time']
    _df.drop(columns=dropped_cols, inplace=True)
    _df.set_index('Datetime', inplace=True)
    return _df

# read NCEP data
col_names = ['Date', 'Time','Tncep', 'RH', 'Pressure', 'WS', 'WD', 'rain_fall', 'snow_fall', 'snow_depth', 'Incep']
ncep_df = read_ncep_data("/content/drive/MyDrive/NN_prophet_train_pv/pvdata_folder/siteCU03_2023-01-01to2023-12-31.csv")
ncep_df['Tncep'] = ncep_df['Tncep']-273.5
ncep_df['Incep'] = ncep_df['Incep'] * 4
ncep_df
ncep_df = ncep_df.reset_index()
ncep_df = ncep_df.rename(columns={'Datetime': 'datetime'})

### Clear sky model (Iclr) => solar_info_df

In [ ]:
import pandas as pd
import numpy as np
class SolarCalculator:
    """

    this


    """
    _gridtiff_metadata_df = pd.read_csv('/content/drive/MyDrive/NN_prophet_train_pv/pvdata_folder/gridtiff_metadata.csv')

    _lat_metadata_arr = (_gridtiff_metadata_df['lat']*np.pi/180).to_numpy().reshape(-1,1)
    _long_metadata_arr = (_gridtiff_metadata_df['long']*np.pi/180).to_numpy().reshape(-1,1)

    _alt_metadata_arr = _gridtiff_metadata_df['alt'].to_numpy()
    _solarmap_TL_metadata_arr = _gridtiff_metadata_df['nearest_TL'].to_numpy()

    _JanJai_metadata_df = pd.read_csv('/content/drive/MyDrive/NN_prophet_train_pv/pvdata_folder/JanjaiAngstromTurbidity.csv')
    _JanJai_lat_metadata_arr = (_JanJai_metadata_df['Latitude']*np.pi/180).to_numpy().reshape(-1,1)
    _JanJai_long_metadata_arr = (_JanJai_metadata_df['Longitude']*np.pi/180).to_numpy().reshape(-1,1)


    def __init__(self, lat, long):
        self.lat = lat
        self.long = long
        self.nearest_alt, self.nearest_solarmap_TL = self.get_nearest_measurement_metadata()
        self.month_TL = self.get_nearest_JanJai_metadata()

    def get_nearest_measurement_metadata(self):
        user_rad_lat = self.lat*np.pi/180
        user_rad_long = self.long*np.pi/180
        dist_arr = np.arccos(np.sin(user_rad_lat)*np.sin(SolarCalculator._lat_metadata_arr)+
                     np.cos(user_rad_lat)*np.cos(SolarCalculator._lat_metadata_arr )*np.cos(abs(user_rad_long-SolarCalculator._long_metadata_arr)))
        nearest_index = np.argmin(dist_arr)
        nearest_alt = SolarCalculator._alt_metadata_arr[nearest_index]
        nearest_solarmap_TL = SolarCalculator._solarmap_TL_metadata_arr[nearest_index]
        return nearest_alt, nearest_solarmap_TL

    def get_nearest_JanJai_metadata(self):
        user_rad_lat = self.lat*np.pi/180
        user_rad_long = self.long*np.pi/180
        dist_arr = np.arccos(np.sin(user_rad_lat)*np.sin(SolarCalculator._JanJai_lat_metadata_arr)+
                     np.cos(user_rad_lat)*np.cos(SolarCalculator._JanJai_lat_metadata_arr )*np.cos(abs(user_rad_long-SolarCalculator._JanJai_long_metadata_arr)))
        nearest_index = np.argmin(dist_arr)
        chosen_beta_df = SolarCalculator._JanJai_metadata_df.loc[nearest_index, ['Jan','Feb','Mar','Apr','May','Jun','Jul','Aug','Sep','Oct','Nov','Dec']]

        AngstromTurbidity = chosen_beta_df.to_numpy()

        # Precitable Water (cm) were downloaded from AERONET (averaged over 2019-2022) at BKK lat/long
        PW = np.array( [3.0429, 3.3528, 4.0548, 4.5590, 5.2208, 5.5694, 4.7205, 5.2554, 5.1380, 4.7121, 4.2269, 3.2973 ] )
        # Remund Formula of TL for each month -- returned as 12-entry array

        month_TL = (1.8494+0.24245 * PW - 0.0203 * PW**2) + (15.427+0.3153 * PW - 0.0254 * PW ** 2) * AngstromTurbidity
        return month_TL



    def cal_dzna(self, start_date, end_date, freq='15T'):
        phi = self.lat
        date_range = pd.date_range(start=start_date, end=end_date, freq=freq)
        doy_arr = date_range.dayofyear.to_numpy()
        hour_arr = date_range.hour.to_numpy()
        minute_arr = date_range.minute.to_numpy()

        time_arr = hour_arr + minute_arr/60
        B = (360/365)*(doy_arr-81)
        LSTM = 15*7
        EoT = 9.87*np.sin(2*B*np.pi/180)-7.53*np.cos(B*np.pi/180)-1.5*np.sin(B*np.pi/180)
        TC = 4*(self.long-LSTM)+EoT
        LST = time_arr + TC/60
        HRA = 15*abs(LST-12)
        delta= -23.45*np.cos(2*np.pi*(doy_arr+10)/365)
        zna = np.sin(delta*np.pi/180)*np.sin(phi*np.pi/180) + np.cos(delta*np.pi/180)*np.cos(phi*np.pi/180)*np.cos(HRA*np.pi/180)
        zna_arr = np.arccos(zna)*180/np.pi

        zna_df = pd.DataFrame({'Datetime':date_range, 'zna':zna_arr})
        zna_df.set_index('Datetime', inplace=True)

        return zna_df

    def cal_dairmass(self, start_date, end_date, freq='15T'):
        phi = self.lat
        date_range = pd.date_range(start=start_date, end=end_date, freq=freq)
        doy_arr = date_range.dayofyear.to_numpy()
        hour_arr = date_range.hour.to_numpy()
        minute_arr = date_range.minute.to_numpy()
        time_arr = hour_arr + minute_arr/60
        B = (360/365)*(doy_arr - 81)
        LSTM = 15*7
        EoT = 9.87*np.sin(2*B*np.pi/180)-7.53*np.cos(B*np.pi/180)-1.5*np.sin(B*np.pi/180)
        TC = 4*(self.long-LSTM)+EoT
        LST = time_arr + TC/60
        HRA = 15*abs(LST-12)
        delta= -23.45*np.cos(2*np.pi*(doy_arr+10)/365)
        x = np.sin(delta*np.pi/180)*np.sin(phi*np.pi/180) + np.cos(delta*np.pi/180)*np.cos(phi*np.pi/180)*np.cos(HRA*np.pi/180)
        x = np.where(x<0, 0, x)
        AM_arr = 1 / (x + 0.50572 * (96.07995 - np.degrees(np.arccos(x))) ** -1.6364)
        AM_df = pd.DataFrame({'Datetime':date_range, 'AM':AM_arr})
        AM_df.set_index('Datetime', inplace=True)
        return AM_df



    def cal_clearsky_irradiance(self, start_date, end_date, freq='15T', method='solarmap'):
        phi = self.lat
        date_range = pd.date_range(start=start_date, end=end_date, freq=freq)
        doy_arr = date_range.dayofyear.to_numpy()
        hour_arr = date_range.hour.to_numpy()
        minute_arr = date_range.minute.to_numpy()
        time_arr = hour_arr + minute_arr/60
        B = (360/365)*(doy_arr - 81)
        LSTM = 15*7
        EoT = 9.87*np.sin(2*B*np.pi/180)-7.53*np.cos(B*np.pi/180)-1.5*np.sin(B*np.pi/180)
        TC = 4*(self.long-LSTM)+EoT
        LST = time_arr + TC/60
        HRA = 15*abs(LST-12)
        delta= -23.45*np.cos(2*np.pi*(doy_arr+10)/365)
        x = np.sin(delta*np.pi/180)*np.sin(phi*np.pi/180) + np.cos(delta*np.pi/180)*np.cos(phi*np.pi/180)*np.cos(HRA*np.pi/180)
        x = np.where(x<0, 0, x)
        AM_arr = 1 / (x + 0.50572 * (96.07995 - np.degrees(np.arccos(x))) ** -1.6364)

        TL_arr = np.zeros(len(date_range))
        if method == 'solarmap':
            TL_arr[:] = self.nearest_solarmap_TL
        elif method == 'JanJai':
            month_arr = date_range.month.to_numpy()
            for month_index in range(12):
                TL_arr = TL_arr + np.equal(month_arr, month_index+1)*self.month_TL[month_index]

        f1 = np.e ** (-self.nearest_alt / 8000)
        f2 = np.e ** (-self.nearest_alt / 1250)
        a1 = (self.nearest_alt * 5.09e-5) + 0.868
        a2 = (self.nearest_alt * 3.92e-5) + 0.0387
        Isc = 1366.1
        iclr_arr = a1 * Isc * x * np.e ** (-a2 * AM_arr * (f1 + f2 * (TL_arr - 1)))

        iclr_df = pd.DataFrame({'Datetime':date_range, 'Iclr':iclr_arr})
        iclr_df.set_index('Datetime', inplace=True)
        return iclr_df

    def get_solar_info(self, start_date, end_date, freq='15T', method='solarmap'):
        zna_df = self.cal_dzna(start_date, end_date, freq)
        AM_df = self.cal_dairmass(start_date, end_date, freq)
        Iclr_df = self.cal_clearsky_irradiance(start_date, end_date, freq, method)

        solar_info_df = zna_df.join(AM_df, how='inner').join(Iclr_df, how='inner')

        return solar_info_df


In [ ]:
site1_obj = SolarCalculator(13.736691018995627, 100.5321481065149)
start_date = '2023-01-01'
end_date = '2024-01-01'
freq = '15min'
method = 'solarmap'
solar_info_df = site1_obj.get_solar_info(start_date, end_date, freq, method)

### Cloud index (CI) => df_ci

In [ ]:
df_ci = pd.read_csv('/content/drive/MyDrive/NN_prophet_train_pv/pvdata_folder/cloud_extracted_CU_003.csv', usecols=['Datetime', 'R_55'], parse_dates=['Datetime'])
df_ci = df_ci.rename(columns={'Datetime': 'datetime', 'R_55': 'CI'})
df_ci['datetime'] = pd.to_datetime(df_ci['datetime'], format='%Y-%m-%d %H:%M:%S')

start_date = '2023-01-01'
end_date = '2024-01-01'

df_ci = df_ci[(df_ci['datetime'] >= start_date) & (df_ci['datetime'] <= end_date)]
df_ci['datetime'] = df_ci['datetime'].dt.tz_localize(None)

### Actual irradiance (Iactual) => df_irradiance

In [ ]:
df_irradiance = pd.read_csv('/content/drive/MyDrive/NN_prophet_train_pv/pvdata_folder/EE Station 1-20230101-20231231_15minresampled.csv', usecols=['Datetime', 'Irradiance_30 (W/m2)'], parse_dates=['Datetime'])
df_irradiance = df_irradiance.rename(columns={'Datetime': 'datetime', 'Irradiance_30 (W/m2)': 'irradiance'})

### Data-preprocessing

In [ ]:
ncep_df = ncep_df[['datetime','Incep']]
ncep_df

datetime     Incep
0     2023-01-01 07:15:00   49.2504
1     2023-01-01 07:30:00   89.4540
2     2023-01-01 07:45:00  135.5100
3     2023-01-01 08:00:00  187.0680
4     2023-01-01 08:15:00  243.7264
...                   ...       ...
35035 2024-01-01 06:00:00    0.0000
35036 2024-01-01 06:15:00    0.0000
35037 2024-01-01 06:30:00    0.0000
35038 2024-01-01 06:45:00    0.0028
35039 2024-01-01 07:00:00   18.8520

[35040 rows x 2 columns]

In [ ]:
solar_info_df = solar_info_df.reset_index()
solar_info_df = solar_info_df.rename(columns = {'Datetime':'datetime'})
df_Iclr = solar_info_df[['datetime','Iclr']]
df_Iclr

datetime  Iclr
0     2023-01-01 00:00:00   0.0
1     2023-01-01 00:15:00   0.0
2     2023-01-01 00:30:00   0.0
3     2023-01-01 00:45:00   0.0
4     2023-01-01 01:00:00   0.0
...                   ...   ...
35036 2023-12-31 23:00:00   0.0
35037 2023-12-31 23:15:00   0.0
35038 2023-12-31 23:30:00   0.0
35039 2023-12-31 23:45:00   0.0
35040 2024-01-01 00:00:00   0.0

[35041 rows x 2 columns]

In [ ]:
df_ci = df_ci.set_index('datetime')
df_ci = df_ci.resample('15min').interpolate(method='linear')
df_ci = df_ci.reset_index()
df_ci

datetime        CI
0     2023-01-01 06:00:00  0.000000
1     2023-01-01 06:15:00  0.019608
2     2023-01-01 06:30:00  0.039216
3     2023-01-01 06:45:00  0.341176
4     2023-01-01 07:00:00  0.643137
...                   ...       ...
34988 2023-12-31 17:00:00  0.662745
34989 2023-12-31 17:15:00  0.511765
34990 2023-12-31 17:30:00  0.360784
34991 2023-12-31 17:45:00  0.243137
34992 2023-12-31 18:00:00  0.125490

[34993 rows x 2 columns]

### Concat all data

In [ ]:
df = pd.merge(df_Iclr,df_ci,on='datetime',how='left')
df = pd.merge(df,ncep_df,on='datetime',how='left')
df = df.fillna(0)
df.isna().sum()

datetime    0
Iclr        0
CI          0
Incep       0
dtype: int64

In [ ]:
start_date_train = '2023-01-01'
end_date_train = '2023-11-30'

start_date_test = '2023-12-01'
end_date_test = '2024-01-01'

df_train = df[(df['datetime'] >= start_date_train) & (df['datetime'] <= end_date_train)]
df_test = df[(df['datetime'] >= start_date_test) & (df['datetime'] <= end_date_test)]

In [ ]:
df_train

datetime  Iclr   CI  Incep
0     2023-01-01 00:00:00   0.0  0.0    0.0
1     2023-01-01 00:15:00   0.0  0.0    0.0
2     2023-01-01 00:30:00   0.0  0.0    0.0
3     2023-01-01 00:45:00   0.0  0.0    0.0
4     2023-01-01 01:00:00   0.0  0.0    0.0
...                   ...   ...  ...    ...
31964 2023-11-29 23:00:00   0.0  0.0    0.0
31965 2023-11-29 23:15:00   0.0  0.0    0.0
31966 2023-11-29 23:30:00   0.0  0.0    0.0
31967 2023-11-29 23:45:00   0.0  0.0    0.0
31968 2023-11-30 00:00:00   0.0  0.0    0.0

[31969 rows x 4 columns]

In [ ]:
df_actual_train = df_irradiance[(df_irradiance['datetime'] >= start_date_train) & (df_irradiance['datetime'] <= end_date_train)]

# impute by previous consecutive day
df_actual_train['datetime'] = pd.to_datetime(df_actual_train.datetime)
df_actual_train = df_actual_train.set_index('datetime')
df_actual_train = df_actual_train.reindex(pd.date_range('2023-01-01 00:00:00',
                         '2023-11-30 00:00:00', freq='15 min')
          ).reset_index().rename(columns={'index':'datetime'})
df_actual_train = df_actual_train.groupby(df_actual_train.datetime.dt.time).ffill()
df_actual_train

WARNING - (py.warnings._showwarnmsg) - <ipython-input-131-393a9e074acc>:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy




A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy




datetime  irradiance
0     2023-01-01 00:00:00    0.800000
1     2023-01-01 00:15:00    0.000000
2     2023-01-01 00:30:00    0.000000
3     2023-01-01 00:45:00    0.000000
4     2023-01-01 01:00:00    0.000000
...                   ...         ...
31964 2023-11-29 23:00:00    3.533333
31965 2023-11-29 23:15:00    3.666667
31966 2023-11-29 23:30:00    2.933333
31967 2023-11-29 23:45:00    3.600000
31968 2023-11-30 00:00:00    0.800000

[31969 rows x 2 columns]

In [ ]:
df_train

datetime  Iclr   CI  Incep
0     2023-01-01 00:00:00   0.0  0.0    0.0
1     2023-01-01 00:15:00   0.0  0.0    0.0
2     2023-01-01 00:30:00   0.0  0.0    0.0
3     2023-01-01 00:45:00   0.0  0.0    0.0
4     2023-01-01 01:00:00   0.0  0.0    0.0
...                   ...   ...  ...    ...
31964 2023-11-29 23:00:00   0.0  0.0    0.0
31965 2023-11-29 23:15:00   0.0  0.0    0.0
31966 2023-11-29 23:30:00   0.0  0.0    0.0
31967 2023-11-29 23:45:00   0.0  0.0    0.0
31968 2023-11-30 00:00:00   0.0  0.0    0.0

[31969 rows x 4 columns]

### NN prophet model

In [ ]:
train_df = pd.merge(df_train, df_actual_train,on='datetime',how='left')
train_df = train_df.rename(columns={'datetime': 'ds', 'irradiance': 'y'})
train_df

ds  Iclr   CI  Incep         y
0     2023-01-01 00:00:00   0.0  0.0    0.0  0.800000
1     2023-01-01 00:15:00   0.0  0.0    0.0  0.000000
2     2023-01-01 00:30:00   0.0  0.0    0.0  0.000000
3     2023-01-01 00:45:00   0.0  0.0    0.0  0.000000
4     2023-01-01 01:00:00   0.0  0.0    0.0  0.000000
...                   ...   ...  ...    ...       ...
31964 2023-11-29 23:00:00   0.0  0.0    0.0  3.533333
31965 2023-11-29 23:15:00   0.0  0.0    0.0  3.666667
31966 2023-11-29 23:30:00   0.0  0.0    0.0  2.933333
31967 2023-11-29 23:45:00   0.0  0.0    0.0  3.600000
31968 2023-11-30 00:00:00   0.0  0.0    0.0  0.800000

[31969 rows x 5 columns]

In [ ]:
fig = px.line(train_df, x='ds', y=['Iclr', 'CI', 'Incep','y'])
fig.show()

WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.10/dist-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result




In [ ]:
model_day_ahead_Incep = NeuralProphet(
    yearly_seasonality=False,  # Turn off yearly seasonality
    weekly_seasonality=False,  # Turn off weekly seasonality
    daily_seasonality=True,  # Enable daily seasonality as solar irradiance may have daily patterns
    n_forecasts=3*4*24,
    n_lags=4*24,
    impute_missing=True,
    )

model_day_ahead_Incep.add_future_regressor('Iclr')
model_day_ahead_Incep.add_future_regressor('Incep')

model_day_ahead_Incep.add_lagged_regressor('CI')


learning_rate = 0.01  # Set an initial learning rate

# Training the model with manual learning rate adjustment
metrics_1 = model_day_ahead_Incep.fit(train_df, freq="15T", learning_rate=learning_rate)


INFO - (NP.forecaster.add_lagged_regressor) - n_lags = 'auto', number of lags for regressor is set to Autoregression number of lags (96)
INFO:NP.forecaster:n_lags = 'auto', number of lags for regressor is set to Autoregression number of lags (96)
WARNING - (NP.forecaster.fit) - When Global modeling with local normalization, metrics are displayed in normalized scale.
WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.10/dist-packages/neuralprophet/df_utils.py:1152: FutureWarning:

Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.



Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.


INFO - (NP.df_utils._infer_frequency) - Major frequency 15min corresponds to 99.997% of the data.
INFO:NP.df_utils:Major frequency 15min corresponds to 99.997% of the data.
WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.10/dist-packages/neura

Training: 0it [00:00, ?it/s]

### Test set

In [ ]:
df_test.isna().sum()

datetime    0
Iclr        0
CI          0
Incep       0
dtype: int64

In [ ]:
df_test

datetime  Iclr   CI  Incep
32064 2023-12-01 00:00:00   0.0  0.0    0.0
32065 2023-12-01 00:15:00   0.0  0.0    0.0
32066 2023-12-01 00:30:00   0.0  0.0    0.0
32067 2023-12-01 00:45:00   0.0  0.0    0.0
32068 2023-12-01 01:00:00   0.0  0.0    0.0
...                   ...   ...  ...    ...
35036 2023-12-31 23:00:00   0.0  0.0    0.0
35037 2023-12-31 23:15:00   0.0  0.0    0.0
35038 2023-12-31 23:30:00   0.0  0.0    0.0
35039 2023-12-31 23:45:00   0.0  0.0    0.0
35040 2024-01-01 00:00:00   0.0  0.0    0.0

[2977 rows x 4 columns]

In [ ]:
df_actual_test = df_irradiance[(df_irradiance['datetime'] >= start_date_test) & (df_irradiance['datetime'] <= end_date_test)]
df_actual_test

datetime  irradiance
32064 2023-12-01 00:00:00    0.000000
32065 2023-12-01 00:15:00    0.000000
32066 2023-12-01 00:30:00    0.000000
32067 2023-12-01 00:45:00    0.000000
32068 2023-12-01 01:00:00    0.000000
...                   ...         ...
35035 2023-12-31 22:45:00    0.200000
35036 2023-12-31 23:00:00    0.466667
35037 2023-12-31 23:15:00    0.133333
35038 2023-12-31 23:30:00    0.533333
35039 2023-12-31 23:45:00    0.600000

[2976 rows x 2 columns]

In [ ]:
df_test = pd.merge(df_test,df_actual_test,on='datetime',how='left')
df_test

datetime  Iclr   CI  Incep  irradiance
0    2023-12-01 00:00:00   0.0  0.0    0.0    0.000000
1    2023-12-01 00:15:00   0.0  0.0    0.0    0.000000
2    2023-12-01 00:30:00   0.0  0.0    0.0    0.000000
3    2023-12-01 00:45:00   0.0  0.0    0.0    0.000000
4    2023-12-01 01:00:00   0.0  0.0    0.0    0.000000
...                  ...   ...  ...    ...         ...
2972 2023-12-31 23:00:00   0.0  0.0    0.0    0.466667
2973 2023-12-31 23:15:00   0.0  0.0    0.0    0.133333
2974 2023-12-31 23:30:00   0.0  0.0    0.0    0.533333
2975 2023-12-31 23:45:00   0.0  0.0    0.0    0.600000
2976 2024-01-01 00:00:00   0.0  0.0    0.0         NaN

[2977 rows x 5 columns]

In [ ]:
df_test = df_test.rename(columns={'datetime':'ds','irradiance':'y'})
df_test

ds  Iclr   CI  Incep         y
0    2023-12-01 00:00:00   0.0  0.0    0.0  0.000000
1    2023-12-01 00:15:00   0.0  0.0    0.0  0.000000
2    2023-12-01 00:30:00   0.0  0.0    0.0  0.000000
3    2023-12-01 00:45:00   0.0  0.0    0.0  0.000000
4    2023-12-01 01:00:00   0.0  0.0    0.0  0.000000
...                  ...   ...  ...    ...       ...
2972 2023-12-31 23:00:00   0.0  0.0    0.0  0.466667
2973 2023-12-31 23:15:00   0.0  0.0    0.0  0.133333
2974 2023-12-31 23:30:00   0.0  0.0    0.0  0.533333
2975 2023-12-31 23:45:00   0.0  0.0    0.0  0.600000
2976 2024-01-01 00:00:00   0.0  0.0    0.0       NaN

[2977 rows x 5 columns]

### Save Forecast

In [ ]:
#forecast.loc[:,['ds']+ [f"yhat{i+1}" for i in range(12)]].to_csv('load_NearRT_20231031_20231230.csv',index=False)

In [ ]:
# raw true based on forecast start
# default based on datetime target
#forecast = nnProphet_model.predict(test_data,raw = True)

# Predict base-on datetime target
forecast = model_day_ahead_Incep.predict(df_test)
forecast = forecast.dropna()
forecast

WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.10/dist-packages/neuralprophet/df_utils.py:1152: FutureWarning:

Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.



Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.


INFO - (NP.df_utils._infer_frequency) - Major frequency 15min corresponds to 99.966% of the data.
INFO:NP.df_utils:Major frequency 15min corresponds to 99.966% of the data.
WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.10/dist-packages/neuralprophet/df_utils.py:1173: FutureWarning:

'T' is deprecated and will be removed in a future version, please use 'min' instead.



'T' is deprecated and will be removed in a future version, please use 'min' instead.


WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.10/dist-packages/neuralprophet/df_utils.py:1152: FutureWarning:

Series.view is deprecate

Predicting: 247it [00:00, ?it/s]

เอาต์พุตของการสตรีมมีการตัดเหลือเพียง 5000 บรรทัดสุดท้าย
DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`



DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`


WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.10/dist-packages/neuralprophet/data/process.py:127: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`



DataFrame is highly fragmente

ds         y      yhat1     yhat2     yhat3      yhat4  \
383  2023-12-04 23:45:00  1.333333   1.434610  6.759247  8.820391  11.323559   
384  2023-12-05 00:00:00  0.266667   8.515334  6.433722  8.702048   5.393414   
385  2023-12-05 00:15:00  0.000000   3.272832  0.701894 -2.058728   0.006123   
386  2023-12-05 00:30:00  0.000000  -1.221596  0.784942  1.745009   1.594966   
387  2023-12-05 00:45:00  0.000000  12.550341  3.066336  0.490898  -5.199169   
...                  ...       ...        ...       ...       ...        ...   
2685 2023-12-28 23:15:00  0.266667  -5.323057 -0.771002  0.620078   1.608118   
2686 2023-12-28 23:30:00  0.533333  12.254157  4.550452  3.192327   0.788890   
2687 2023-12-28 23:45:00  0.133333  -3.019778  2.776075  2.385137   1.838083   
2688 2023-12-29 00:00:00  0.000000   6.111046  2.587121  2.443262   0.555655   
2689 2023-12-29 00:15:00  0.000000  -1.890285 -3.851039 -3.500896  -3.456379   

          yhat5      yhat6     yhat7      yhat8  ...  lagged_regressor_CI284  \
383    4.797049   6.642055  9.535323  15.428463  ...                3.925800   
384   14.528207  12.785751  5.565741   5.021485  ...                4.284374   
385    4.823236   0.270301  6.949929   6.314228  ...                5.357545   
386    3.122812  10.118192  4.108414   2.546759  ...                7.144068   
387    3.587248  -3.499495  1.350789   3.512682  ...               12.032902   
...         ...        ...       ...        ...  ...                     ...   
2685   2.201369   6.735093  3.429433   3.989655  ...                1.541163   
2686   4.440224  -4.240461 -2.050886   1.551003  ...               21.913895   
2687   3.207853   7.480463  9.079424   2.197027  ...                8.679950   
2688   6.199659   1.328718 -0.651141   4.980789  ...               20.024017   
2689  -2.876087  -3.910501 -0.862600  -3.925141  ...                4.610336   

      lagged_regressor_CI285  lagged_regressor_CI286  lagged_regressor_CI287  \
383                10.632186                6.280627               10.913271   
384                 0.005596                1.002286                1.968763   
385                 5.110862                6.142118                9.849866   
386                10.652503                7.619976                9.782005   
387                 6.611538               10.677811               12.340928   
...                      ...                     ...                     ...   
2685                6.102398                2.226494                7.793701   
2686               11.251844               16.243662               15.108603   
2687               19.819082               10.497629               21.077309   
2688                8.558332               14.918460               11.361251   
2689               10.837966                5.915618               12.919436   

      lagged_regressor_CI288      trend  season_daily  \
383                11.576814  34.886795    -45.397953   
384                 3.658966  34.887867    -46.800400   
385                 5.467083  34.888939    -47.934109   
386                15.721559  34.890011    -49.268841   
387                 5.009069  34.891083    -49.848347   
...                      ...        ...           ...   
2685               12.962996  37.352924    -42.916988   
2686               15.315192  37.353996    -43.908527   
2687               18.932734  37.355068    -45.449821   
2688               18.584089  37.356136    -46.651150   
2689                3.102563  37.357212    -47.902737   

      future_regressors_additive  future_regressor_Iclr  \
383                          0.0                    0.0   
384                          0.0                    0.0   
385                          0.0                    0.0   
386                          0.0                    0.0   
387                          0.0                    0.0   
...                          ...                    ...   
2685                         0.0         

In [ ]:
# forecast.loc[:,['ds']+ [f"yhat{i+1}" for i in range(288)]].to_csv('load_Dayahead_20231101_20231228.csv',index=False)

In [ ]:
forecast_filter = forecast[(forecast['ds'].dt.hour >= 7) & (forecast['ds'].dt.hour <= 17) & (forecast['y'] != 0)]

## Total error

In [ ]:
error_df = pd.DataFrame()
norm_factor = forecast_filter['y'].max() - forecast_filter['y'].min()
#get e = y_true - y_pred
for i in range(288) :
  error_df[f'e{i+1}'] =  forecast_filter['y'] - forecast_filter[f'yhat{i+1}']

error_df

WARNING - (py.warnings._showwarnmsg) - <ipython-input-145-85f16d5d3370>:5: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`



DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`


WARNING - (py.warnings._showwarnmsg) - <ipython-input-145-85f16d5d3370>:5: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`



DataFrame is highly fragmente

e1         e2         e3         e4         e5         e6  \
412  -20.364931  -7.116663   3.227995  -5.555140  -5.183497   1.859354   
413  -20.471784 -27.131948 -22.272566 -15.443022 -27.748930 -28.271871   
414   43.643481  34.735019  26.909641  36.321399  28.947086  32.444202   
415   36.678317  73.049884  69.039432  61.912494  69.285922  69.998096   
416   15.746625  36.162854  53.527158  53.864560  38.086163  51.723477   
...         ...        ...        ...        ...        ...        ...   
2659 -54.416399 -77.128817 -75.754580 -73.169619 -74.912203 -64.724848   
2660   0.255038 -40.183251 -60.339799 -60.390031 -51.918107 -49.538972   
2661   6.761782   7.634011 -19.853341 -33.156789 -39.965902 -32.946042   
2662  16.915773  19.912226  16.571923 -11.836953 -20.434232 -23.912751   
2663  11.973940  23.788748  27.608493  25.158054   0.427160 -11.144728   

             e7         e8         e9        e10  ...       e279       e280  \
412   -2.183169   0.141104  -7.147059  -7.527140  ...   2.740965   6.696073   
413  -30.134474 -31.602880 -24.917684 -32.459783  ...  -1.777944 -15.391989   
414   31.656848  31.577335  27.182101  28.626041  ...  32.328067  38.645679   
415   60.717761  62.617297  63.906619  61.267856  ...  81.369708  83.434421   
416   50.104993  41.236417  50.098004  44.460080  ...  68.402142  58.023755   
...         ...        ...        ...        ...  ...        ...        ...   
2659 -58.797487 -43.749254 -42.427240 -35.777636  ... -53.352015 -48.021952   
2660 -39.095880 -43.364259 -30.719712 -30.370423  ... -36.813775 -38.959786   
2661 -35.676122 -27.051835 -25.274072 -16.102575  ... -19.548345 -22.471277   
2662 -19.716119 -13.825963  -8.770379 -11.183202  ... -17.694352  -9.434587   
2663  -7.445481  -7.643469  -7.646357  -3.893109  ...  16.293929   5.464524   

           e281       e282       e283       e284       e285       e286  \
412    2.331159 -13.599657  -7.035387  -1.326731  -8.403093  -7.146166   
413  -27.036535 -14.108709 -21.096403 -25.038900 -20.491987 -24.668737   
414   42.713580  21.281970  31.318240  31.585208  23.357227  27.245929   
415   83.487247  75.503711  72.265399  70.981570  72.008807  67.536517   
416   61.231122  77.873532  71.100354  62.827588  62.145520  60.687573   
...         ...        ...        ...        ...        ...        ...   
2659 -57.040415 -49.712702 -61.458933 -58.457537 -46.649820 -46.693583   
2660 -31.620469 -49.628678 -37.297662 -34.234506 -32.624284 -30.073403   
2661 -32.129255 -28.585725 -30.754178 -34.215215 -37.892057 -28.337999   
2662  -5.400643 -18.189939 -16.531003 -10.924523  -5.669637 -10.657170   
2663   4.694473   2.205633   7.417094   5.230715  -2.918580   5.087724   

           e287       e288  
412   -2.043886  -0.712633  
413  -24.134146 -19.643659  
414   29.453052  26.960071  
415   64.272617  71.215640  
416   59.633542  53.006726  
...         ...        ...  
2659 -48.863825 -61.784250  
2660 -34.393739 -32.379190  
2661 -16.921769 -30.437078  
2662 -11.710504  -2.451819  
2663   2.674511   5.163587  

[1056 rows x 288 columns]

In [ ]:
# MAE
MAE = np.mean(np.abs(error_df),axis=0)
# RMSE
RMSE = np.sqrt( np.mean(error_df**2,axis=0))
# MAPE
MAPE = np.mean(np.abs(error_df.div(forecast['y'],axis=0)), axis=0)*100
# MBE
MBE = np.mean(error_df,axis=0)
# minmax NMAE
NMAE =  np.mean(np.abs(error_df),axis=0)/norm_factor
error_table = pd.DataFrame({'step':range(1,289),'MAE':MAE,'RMSE':RMSE,'MAPE':MAPE,'MBE':MBE,'NMAE':NMAE})



In [ ]:
error_table[(error_table['step'] == 96)| (error_table['step'] == 192) | (error_table['step'] == 288)]

step        MAE        RMSE       MAPE        MBE      NMAE
e96     96  77.172494  101.343775  32.503198  20.116429  0.089155
e192   192  81.593864  105.506474  34.393504  19.439471  0.094263
e288   288  81.235109  105.249195  32.376336  20.082020  0.093848

##Error by hour

In [ ]:
df_eval = forecast_filter[['ds',    'y'] + [ f'yhat{i+1}' for i in range(288)]]
error_df = pd.DataFrame()
error_df['ds'] = df_eval['ds']
error_df['y'] = df_eval['y']
#get e = y_true - y_pred
for i in range(288) :
  error_df[f'e{i+1}'] =  forecast_filter['y'] - forecast_filter[f'yhat{i+1}']

error_df

WARNING - (py.warnings._showwarnmsg) - <ipython-input-148-42dcede485aa>:7: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`



DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`


WARNING - (py.warnings._showwarnmsg) - <ipython-input-148-42dcede485aa>:7: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`



DataFrame is highly fragmente

ds           y         e1         e2         e3  \
412  2023-12-05 07:00:00   62.866667 -20.364931  -7.116663   3.227995   
413  2023-12-05 07:15:00   76.133333 -20.471784 -27.131948 -22.272566   
414  2023-12-05 07:30:00  176.200000  43.643481  34.735019  26.909641   
415  2023-12-05 07:45:00  251.200000  36.678317  73.049884  69.039432   
416  2023-12-05 08:00:00  296.800000  15.746625  36.162854  53.527158   
...                  ...         ...        ...        ...        ...   
2659 2023-12-28 16:45:00   56.866667 -54.416399 -77.128817 -75.754580   
2660 2023-12-28 17:00:00   40.933333   0.255038 -40.183251 -60.339799   
2661 2023-12-28 17:15:00   33.666667   6.761782   7.634011 -19.853341   
2662 2023-12-28 17:30:00   23.933333  16.915773  19.912226  16.571923   
2663 2023-12-28 17:45:00   13.466667  11.973940  23.788748  27.608493   

             e4         e5         e6         e7         e8  ...       e279  \
412   -5.555140  -5.183497   1.859354  -2.183169   0.141104  ...   2.740965   
413  -15.443022 -27.748930 -28.271871 -30.134474 -31.602880  ...  -1.777944   
414   36.321399  28.947086  32.444202  31.656848  31.577335  ...  32.328067   
415   61.912494  69.285922  69.998096  60.717761  62.617297  ...  81.369708   
416   53.864560  38.086163  51.723477  50.104993  41.236417  ...  68.402142   
...         ...        ...        ...        ...        ...  ...        ...   
2659 -73.169619 -74.912203 -64.724848 -58.797487 -43.749254  ... -53.352015   
2660 -60.390031 -51.918107 -49.538972 -39.095880 -43.364259  ... -36.813775   
2661 -33.156789 -39.965902 -32.946042 -35.676122 -27.051835  ... -19.548345   
2662 -11.836953 -20.434232 -23.912751 -19.716119 -13.825963  ... -17.694352   
2663  25.158054   0.427160 -11.144728  -7.445481  -7.643469  ...  16.293929   

           e280       e281       e282       e283       e284       e285  \
412    6.696073   2.331159 -13.599657  -7.035387  -1.326731  -8.403093   
413  -15.391989 -27.036535 -14.108709 -21.096403 -25.038900 -20.491987   
414   38.645679  42.713580  21.281970  31.318240  31.585208  23.357227   
415   83.434421  83.487247  75.503711  72.265399  70.981570  72.008807   
416   58.023755  61.231122  77.873532  71.100354  62.827588  62.145520   
...         ...        ...        ...        ...        ...        ...   
2659 -48.021952 -57.040415 -49.712702 -61.458933 -58.457537 -46.649820   
2660 -38.959786 -31.620469 -49.628678 -37.297662 -34.234506 -32.624284   
2661 -22.471277 -32.129255 -28.585725 -30.754178 -34.215215 -37.892057   
2662  -9.434587  -5.400643 -18.189939 -16.531003 -10.924523  -5.669637   
2663   5.464524   4.694473   2.205633   7.417094   5.230715  -2.918580   

           e286       e287       e288  
412   -7.146166  -2.043886  -0.712633  
413  -24.668737 -24.134146 -19.643659  
414   27.245929  29.453052  26.960071  
415   67.536517  64.272617  71.215640  
416   60.687573  59.633542  53.006726  
...         ...        ...        ...  
2659 -46.693583 -48.863825 -61.784250  
2660 -30.073403 -34.393739 -32.379190  
2661 -28.337999 -16.921769 -30.437078  
2662 -10.657170 -11.710504  -2.451819  
2663   5.087724   2.674511   5.163587  

[1056 rows x 290 columns]

In [ ]:
K = 288 # number of step ahead
ds_hour = pd.DataFrame({'hour of target':[f'{hour:02}:00' for hour in range(7,18)]})
# calculate metric by hour
# iterate over hour
MAE = []
RMSE = []
MAPE = []
MBE = []
NMAE = []
for hour in range(7,18) :
  hour_df = error_df[error_df['ds'].dt.hour == hour][[f'e{k+1}'  for k in range(K)]]
  y = error_df[error_df['ds'].dt.hour == hour]['y']
  print
  norm_factor = y.max() - y.min()
  # MAE
  MAE.append( np.mean(np.abs(hour_df),axis=0))
  # RMSE
  RMSE.append(np.sqrt( np.mean(hour_df**2,axis=0)) )
  # MAPE
  MAPE.append( np.mean(np.abs(hour_df.div(y,axis=0)), axis=0)*100 )
  # MBE
  MBE.append(np.mean(hour_df,axis=0) )
  # minmax NMAE
  NMAE.append ( np.mean(np.abs(hour_df),axis=0)/norm_factor)
MAE = pd.DataFrame(MAE)
RMSE = pd.DataFrame(RMSE)
MAPE = pd.DataFrame(MAPE)
MBE = pd.DataFrame(MBE)
NMAE = pd.DataFrame(NMAE)
MAE['hour of target'] = ds_hour
RMSE['hour of target'] = ds_hour
MAPE['hour of target'] = ds_hour
MBE['hour of target'] = ds_hour
NMAE['hour of target'] = ds_hour

In [ ]:
# Select type of errors to show
selected_error = 'MAE'
df_select_error = MAE

In [ ]:
df_select_error

e1          e2          e3          e4          e5          e6  \
0   20.835562   26.703558   28.003752   26.710189   27.226096   25.785663   
1   19.151001   31.627173   42.931729   51.137289   52.487096   55.801849   
2   24.712120   35.783210   40.478935   43.712261   46.776856   52.588245   
3   42.627097   56.271227   64.765920   70.892251   72.453631   75.983770   
4   66.608443   82.605962   91.858590   99.940671  103.141480  109.819567   
5   74.749361   94.638820  107.051225  113.635324  111.980420  113.015164   
6   75.576398   80.720916   89.824842   92.790777   95.910664   93.959895   
7   84.502956  103.081596  103.850325  102.540319  105.550131  105.074367   
8   58.919197   80.398092   90.460874   92.293629   88.792515   84.951268   
9   34.507258   45.785113   44.204419   42.302156   41.578169   44.443907   
10  14.453960   25.569559   32.030211   32.414650   30.814241   27.281513   

            e7          e8          e9         e10  ...        e280  \
0    24.766694   24.650920   24.876204   26.177318  ...   29.169554   
1    54.332427   49.150388   48.707599   46.852771  ...   59.463284   
2    55.268188   61.714542   63.471442   61.488117  ...   72.007109   
3    77.924861   79.194691   81.492101   83.354664  ...  111.079639   
4   111.766159  115.071887  117.518301  117.919996  ...  138.040348   
5   115.976302  116.967078  119.692723  121.793245  ...  133.481143   
6    96.279842   96.505627   98.654061   97.946473  ...  100.338577   
7   106.643299  105.591859  106.878130  107.258286  ...  114.909236   
8    84.636686   80.329160   79.176226   77.109894  ...   83.332057   
9    47.510296   45.376208   41.914895   41.712391  ...   41.784303   
10   25.111179   24.323521   21.732305   21.104992  ...   17.770143   

          e281        e282        e283        e284        e285        e286  \
0    29.884417   29.665671   28.488742   28.857037   29.091865   28.633433   
1    58.502837   58.773081   60.042303   60.860464   59.377666   58.339773   
2    72.928872   72.082649   74.265682   74.161651   73.704705   72.987337   
3   110.661655  109.140223  111.586346  112.168592  111.116498  110.913421   
4   137.165757  134.643925  136.851800  137.418299  136.368274  136.621076   
5   134.068190  133.065889  133.757769  133.859835  133.006461  132.785462   
6   100.103962   98.451735  100.665823  101.517241  100.440327  100.826811   
7   114.442113  114.273776  114.926378  115.397448  114.953564  114.976768   
8    84.538745   82.804222   84.446204   84.467368   83.897889   83.948826   
9    41.989970   43.083449   42.512109   42.220552   41.485312   41.633090   
10   18.634306   16.260319   17.182582   17.369395   17.192808   16.699701   

          e287        e288  hour of target  
0    28.653299   28.552131           07:00  
1    58.722545   57.930759           08:00  
2    72.860367   73.053251           09:00  
3   111.203601  111.000648           10:00  
4   136.319216  137.400032           11:00  
5   131.738899  129.750626           12:00  
6   100.220242   99.809696           13:00  
7   114.447408  113.882059           14:00  
8    83.826659   82.746963           15:00  
9    41.547535   41.839820           16:00  
10   16.167966   17.620214           17:00  

[11 rows x 289 columns]

In [ ]:
# df_select_error.to_csv('dayahead_MAE.csv')

In [ ]:
import plotly.graph_objects as go

# Assuming mae_hour_df is your DataFrame
step = [1,2,3]
fig = go.Figure()

selected_errors_with_unit = ['MAE', 'RMSE', 'MBE']
selected_error_with_percentage = ['MAPE']

for k in step:
    fig.add_trace(go.Bar(x=df_select_error['hour of target'], y=df_select_error[f'e{k*96}'], name=str(k) +'day ahead' ))

    if selected_error in selected_errors_with_unit:
        yaxis_option = f'{selected_error} [W/sqm]'
    elif selected_error in selected_error_with_percentage:
        yaxis_option = f'{selected_error} [%]'
    else:
        yaxis_option = f'{selected_error} [no unit]'

fig.update_layout(
    title=f'{selected_error} of irradiance by Hour',
    xaxis_title='Hour of Target',
    yaxis_title=yaxis_option,
    barmode='group',
    width=2480,
    height=1000,
    font={'size': 30})
fig.update_layout(
    plot_bgcolor='white',
    xaxis=dict(
        linecolor='black',
        showgrid=True,
        gridcolor='lightgrey'
    ),
    yaxis=dict(
        linecolor='black',
        showgrid=True,
        gridcolor='lightgrey'
    )
)
fig.show()

In [ ]:
# df_eval.to_csv('dayahead_timeseries.csv')

In [ ]:
import numpy as np
import pandas as pd
from sklearn.metrics import mean_absolute_error, mean_squared_error
import plotly.graph_objects as go

# Assuming result_df is your DataFrame

# Create Plotly time series plot
ts_fig = go.Figure()
step = [96,192,288]
ts_fig.add_trace(go.Scatter(x=df_eval['ds'], y=df_eval['y'], name='Actual', mode='lines',line=dict(color='#000000')))
for k in step :
  ts_fig.add_trace(go.Scatter(x=df_eval['ds'], y=df_eval[f'yhat{k}'], name=str(k//96) +' day ahead', mode='lines'))

ts_fig.update_layout(title='Actual vs Forecasted irradiance in December 2023',
                  xaxis_title='Datetime',
                  yaxis_title='Irradiance (W/sqm)',
                  width=2480,
                  height=1000,
                  font = {'size' : 30})

ts_fig.update_layout(
    plot_bgcolor='white',
    xaxis=dict(
        linecolor='black',
        showgrid=True,
        gridcolor='lightgrey'
    ),
    yaxis=dict(
        linecolor='black',
        showgrid=True,
        gridcolor='lightgrey'
    )
)

ts_fig.show()

WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.10/dist-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result




In [ ]:
forecast

ds         y      yhat1     yhat2     yhat3      yhat4  \
383  2023-12-04 23:45:00  1.333333   1.434610  6.759247  8.820391  11.323559   
384  2023-12-05 00:00:00  0.266667   8.515334  6.433722  8.702048   5.393414   
385  2023-12-05 00:15:00  0.000000   3.272832  0.701894 -2.058728   0.006123   
386  2023-12-05 00:30:00  0.000000  -1.221596  0.784942  1.745009   1.594966   
387  2023-12-05 00:45:00  0.000000  12.550341  3.066336  0.490898  -5.199169   
...                  ...       ...        ...       ...       ...        ...   
2685 2023-12-28 23:15:00  0.266667  -5.323057 -0.771002  0.620078   1.608118   
2686 2023-12-28 23:30:00  0.533333  12.254157  4.550452  3.192327   0.788890   
2687 2023-12-28 23:45:00  0.133333  -3.019778  2.776075  2.385137   1.838083   
2688 2023-12-29 00:00:00  0.000000   6.111046  2.587121  2.443262   0.555655   
2689 2023-12-29 00:15:00  0.000000  -1.890285 -3.851039 -3.500896  -3.456379   

          yhat5      yhat6     yhat7      yhat8  ...  lagged_regressor_CI284  \
383    4.797049   6.642055  9.535323  15.428463  ...                3.925800   
384   14.528207  12.785751  5.565741   5.021485  ...                4.284374   
385    4.823236   0.270301  6.949929   6.314228  ...                5.357545   
386    3.122812  10.118192  4.108414   2.546759  ...                7.144068   
387    3.587248  -3.499495  1.350789   3.512682  ...               12.032902   
...         ...        ...       ...        ...  ...                     ...   
2685   2.201369   6.735093  3.429433   3.989655  ...                1.541163   
2686   4.440224  -4.240461 -2.050886   1.551003  ...               21.913895   
2687   3.207853   7.480463  9.079424   2.197027  ...                8.679950   
2688   6.199659   1.328718 -0.651141   4.980789  ...               20.024017   
2689  -2.876087  -3.910501 -0.862600  -3.925141  ...                4.610336   

      lagged_regressor_CI285  lagged_regressor_CI286  lagged_regressor_CI287  \
383                10.632186                6.280627               10.913271   
384                 0.005596                1.002286                1.968763   
385                 5.110862                6.142118                9.849866   
386                10.652503                7.619976                9.782005   
387                 6.611538               10.677811               12.340928   
...                      ...                     ...                     ...   
2685                6.102398                2.226494                7.793701   
2686               11.251844               16.243662               15.108603   
2687               19.819082               10.497629               21.077309   
2688                8.558332               14.918460               11.361251   
2689               10.837966                5.915618               12.919436   

      lagged_regressor_CI288      trend  season_daily  \
383                11.576814  34.886795    -45.397953   
384                 3.658966  34.887867    -46.800400   
385                 5.467083  34.888939    -47.934109   
386                15.721559  34.890011    -49.268841   
387                 5.009069  34.891083    -49.848347   
...                      ...        ...           ...   
2685               12.962996  37.352924    -42.916988   
2686               15.315192  37.353996    -43.908527   
2687               18.932734  37.355068    -45.449821   
2688               18.584089  37.356136    -46.651150   
2689                3.102563  37.357212    -47.902737   

      future_regressors_additive  future_regressor_Iclr  \
383                          0.0                    0.0   
384                          0.0                    0.0   
385                          0.0                    0.0   
386                          0.0                    0.0   
387                          0.0                    0.0   
...                          ...                    ...   
2685                         0.0         

In [ ]:
forecast.to_csv('dayahead_seasonality.csv')

In [ ]:
ts_fig = go.Figure()

ts_fig.add_trace(go.Scatter(x=forecast['ds'], y=forecast['season_daily'], name='daily_seasonality', mode='lines'))
ts_fig.add_trace(go.Scatter(x=forecast['ds'], y=forecast['trend'], name='trend', mode='lines'))

ts_fig.update_layout(title='Seasonality and trend component of irradiance',
                  xaxis_title='Datetime',
                  yaxis_title='Irradiance (W/sqm)',
                  width=2480,
                  height=1000,
                  font = {'size' : 30}
                     )

ts_fig.update_layout(
    plot_bgcolor='white',
    xaxis=dict(
        linecolor='black',
        showgrid=True,
        gridcolor='lightgrey'
    ),
    yaxis=dict(
        linecolor='black',
        showgrid=True,
        gridcolor='lightgrey'
    )
)




ts_fig.show()

WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.10/dist-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result




# Forecast all

In [ ]:
df = pd.merge(df_Iclr,df_ci,on='datetime',how='left')
df = pd.merge(df,ncep_df,on='datetime',how='left')
df = df.fillna(0)

In [ ]:
start_date = '2023-01-01'
end_date = '2024-01-01'

In [ ]:
df_actual = df_irradiance[(df_irradiance['datetime'] >= start_date) & (df_irradiance['datetime'] <= end_date)]

# impute by previous consecutive day
df_actual['datetime'] = pd.to_datetime(df_actual.datetime)
df_actual = df_actual.set_index('datetime')
df_actual = df_actual.reindex(pd.date_range('2023-01-01 00:00:00',
                         '2024-01-01 00:00:00', freq='15 min')
          ).reset_index().rename(columns={'index':'datetime'})
df_actual = df_actual.groupby(df_actual.datetime.dt.time).ffill()
df_actual

datetime  irradiance
0     2023-01-01 00:00:00    0.800000
1     2023-01-01 00:15:00    0.000000
2     2023-01-01 00:30:00    0.000000
3     2023-01-01 00:45:00    0.000000
4     2023-01-01 01:00:00    0.000000
...                   ...         ...
35036 2023-12-31 23:00:00    0.466667
35037 2023-12-31 23:15:00    0.133333
35038 2023-12-31 23:30:00    0.533333
35039 2023-12-31 23:45:00    0.600000
35040 2024-01-01 00:00:00    0.000000

[35041 rows x 2 columns]

In [ ]:
df = pd.merge(df,df_actual,on='datetime',how='left')
df

datetime  Iclr   CI  Incep  irradiance
0     2023-01-01 00:00:00   0.0  0.0    0.0    0.800000
1     2023-01-01 00:15:00   0.0  0.0    0.0    0.000000
2     2023-01-01 00:30:00   0.0  0.0    0.0    0.000000
3     2023-01-01 00:45:00   0.0  0.0    0.0    0.000000
4     2023-01-01 01:00:00   0.0  0.0    0.0    0.000000
...                   ...   ...  ...    ...         ...
35036 2023-12-31 23:00:00   0.0  0.0    0.0    0.466667
35037 2023-12-31 23:15:00   0.0  0.0    0.0    0.133333
35038 2023-12-31 23:30:00   0.0  0.0    0.0    0.533333
35039 2023-12-31 23:45:00   0.0  0.0    0.0    0.600000
35040 2024-01-01 00:00:00   0.0  0.0    0.0    0.000000

[35041 rows x 5 columns]

In [ ]:
df = df.rename(columns={'datetime':'ds','irradiance':'y'})
df

ds  Iclr   CI  Incep         y
0     2023-01-01 00:00:00   0.0  0.0    0.0  0.800000
1     2023-01-01 00:15:00   0.0  0.0    0.0  0.000000
2     2023-01-01 00:30:00   0.0  0.0    0.0  0.000000
3     2023-01-01 00:45:00   0.0  0.0    0.0  0.000000
4     2023-01-01 01:00:00   0.0  0.0    0.0  0.000000
...                   ...   ...  ...    ...       ...
35036 2023-12-31 23:00:00   0.0  0.0    0.0  0.466667
35037 2023-12-31 23:15:00   0.0  0.0    0.0  0.133333
35038 2023-12-31 23:30:00   0.0  0.0    0.0  0.533333
35039 2023-12-31 23:45:00   0.0  0.0    0.0  0.600000
35040 2024-01-01 00:00:00   0.0  0.0    0.0  0.000000

[35041 rows x 5 columns]

In [ ]:
fig = px.line(df,x='ds',y='y')
fig.show()

WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.10/dist-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result




In [ ]:
forecast = model_day_ahead_Incep.predict(df,raw=True)
forecast = forecast.dropna()
forecast

WARNING - (NP.forecaster.predict) - Raw forecasts are incompatible with plotting utilities
WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.10/dist-packages/neuralprophet/df_utils.py:1152: FutureWarning:

Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.



Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.


INFO - (NP.df_utils._infer_frequency) - Major frequency 15min corresponds to 99.997% of the data.
INFO:NP.df_utils:Major frequency 15min corresponds to 99.997% of the data.
WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.10/dist-packages/neuralprophet/df_utils.py:1173: FutureWarning:

'T' is deprecated and will be removed in a future version, please use 'min' instead.



'T' is deprecated and will be removed in a future version, please use 'min' instead.


WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python

Predicting: 247it [00:00, ?it/s]

INFO - (NP.df_utils.return_df_in_original_format) - Returning df with no ID column
INFO:NP.df_utils:Returning df with no ID column


ds      step0     trend0  season_daily0        ar0  \
0     2023-01-02 00:00:00   3.438361   7.795008     -46.715088  33.690685   
1     2023-01-02 00:15:00  -8.327222   7.810444     -47.869049  33.999443   
2     2023-01-02 00:30:00  -4.757079   7.825879     -48.829403  34.736229   
3     2023-01-02 00:45:00   7.273428   7.841315     -49.253803  35.355320   
4     2023-01-02 01:00:00 -12.088236   7.856750     -49.953552  36.274048   
...                   ...        ...        ...            ...        ...   
34652 2023-12-28 23:00:00   7.838185  37.351852     -42.304405   5.377547   
34653 2023-12-28 23:15:00  -5.323057  37.352924     -42.916988   4.907288   
34654 2023-12-28 23:30:00  12.254157  37.353996     -43.908527   5.933196   
34655 2023-12-28 23:45:00  -3.019778  37.355068     -45.449821   7.183869   
34656 2023-12-29 00:00:00   6.111046  37.356136     -46.651150   7.732721   

       lagged_regressor_CI0  future_regressors_additive0  \
0                  8.667758                          0.0   
1                 -2.268056                          0.0   
2                  1.510217                          0.0   
3                 13.330595                          0.0   
4                 -6.265480                          0.0   
...                     ...                          ...   
34652              7.413190                          0.0   
34653             -4.666279                          0.0   
34654             12.875494                          0.0   
34655             -2.108891                          0.0   
34656              7.673338                          0.0   

       future_regressor_Iclr0  future_regressor_Incep0      step1  ...  \
0                         0.0                      0.0 -11.066348  ...   
1                         0.0                      0.0  -7.214295  ...   
2                         0.0                      0.0  -2.991567  ...   
3                         0.0                      0.0  -4.125079  ...   
4                         0.0                      0.0 -13.145222  ...   
...                       ...                      ...        ...  ...   
34652                     0.0                      0.0  -0.771002  ...   
34653                     0.0                      0.0   4.550452  ...   
34654                     0.0                      0.0   2.776075  ...   
34655                     0.0                      0.0   2.587121  ...   
34656                     0.0                      0.0  -3.851039  ...   

       future_regressor_Iclr286  future_regressor_Incep286    step287  \
0                           0.0                        0.0 -14.300550   
1                           0.0                        0.0 -15.399119   
2                           0.0                        0.0 -27.453333   
3                           0.0                        0.0 -24.238613   
4                           0.0                        0.0 -29.809731   
...                         ...                        ...        ...   
34652                       0.0                        0.0   4.239341   
34653                       0.0                        0.0  -2.552654   
34654                       0.0                        0.0   6.484763   
34655                       0.0                        0.0   1.827837   
34656                       0.0                        0.0   4.115582   

        trend287  season_daily287     ar287  lagged_regressor_CI287  \
0      12.225061       -45.209896  6.365089               12.319199   
1      12.240497       -46.739250  6.277834               12.821803   
2      12.255934       -48.005402  6.125070                2.171064   
3      12.271369       -49.102516  5.750269                6.842265   
4      12.286804       -49.633041  6.396886                1.139623   
...          ...              ...       ...                     ...   
34652  37.659313       -42.446541  1.846518                7.180052   
34653  37.660385       -42.495701  1.582646

In [ ]:
forecast = forecast[['ds']+ [f'step{i}' for i in range(288)]]
forecast

ds      step0      step1      step2      step3  \
0     2023-01-02 00:00:00   3.438361 -11.066348  -9.985935  -9.647479   
1     2023-01-02 00:15:00  -8.327222  -7.214295  -4.983018 -13.433364   
2     2023-01-02 00:30:00  -4.757079  -2.991567 -11.583611 -14.419512   
3     2023-01-02 00:45:00   7.273428  -4.125079  -8.316504 -24.124804   
4     2023-01-02 01:00:00 -12.088236 -13.145222 -26.933571 -16.553461   
...                   ...        ...        ...        ...        ...   
34652 2023-12-28 23:00:00   7.838185  -0.771002   3.192327   1.838083   
34653 2023-12-28 23:15:00  -5.323057   4.550452   2.385137   0.555655   
34654 2023-12-28 23:30:00  12.254157   2.776075   2.443262  -3.456379   
34655 2023-12-28 23:45:00  -3.019778   2.587121  -3.500896  -3.277467   
34656 2023-12-29 00:00:00   6.111046  -3.851039  -2.334482  -2.943175   

           step4      step5      step6      step7      step8  ...    step278  \
0     -12.768863 -24.118729 -27.865728 -17.556297 -15.905308  ... -28.219725   
1     -17.041237 -22.353092 -16.374609 -16.666059 -11.007113  ... -24.201134   
2     -20.174530 -21.866478 -14.233429 -10.318233 -16.230280  ... -17.876560   
3     -17.754839  -9.358789 -11.014566  -9.258828  -7.232441  ... -27.198151   
4      -8.404835 -12.975165  -7.525740 -13.573339 -16.306961  ... -21.186249   
...          ...        ...        ...        ...        ...  ...        ...   
34652   6.199659  -3.910501   4.451104   0.633722  -2.959228  ...  -1.726148   
34653  -2.876087   3.788871  -5.467538  -3.287597  -2.807817  ...   3.600870   
34654   2.503287  -5.512519   4.023465   0.690593  -7.283092  ...  -3.953015   
34655  -1.858843   2.768205  -5.349477 -11.928818  -6.604772  ...   1.888518   
34656  -0.287174  -8.503713  -9.117124  -2.605004  -2.641938  ...  -7.190273   

         step279    step280    step281    step282    step283    step284  \
0     -27.111525 -24.704081 -22.239414 -29.329023 -17.730391 -23.246723   
1     -14.973799 -19.890566 -26.003496 -18.092285 -20.403530 -13.428569   
2     -27.080948 -25.657999 -18.611732 -19.430799 -20.524187 -21.699545   
3     -23.153364 -24.291061 -22.445877 -20.717749 -13.794726 -15.735248   
4     -23.144768 -16.776997 -15.618457 -17.160498 -23.320911 -18.159224   
...          ...        ...        ...        ...        ...        ...   
34652   3.646011   1.753307  -3.566469   1.045199  -3.179250   3.347671   
34653  -3.774328  -1.278197  -0.889458  -6.841521  -2.805997  -3.353244   
34654   0.368534  -8.102369  -5.524510   0.843456   3.545732  -0.346949   
34655  -4.079853  -0.360928   1.416259   0.874434  -7.049906   0.238664   
34656  -7.444260  -5.326583  -1.863012  -4.201056   3.280753  -2.388164   

         step285    step286    step287  
0     -17.201786 -18.406322 -14.300550  
1     -15.401656 -13.641817 -15.399119  
2     -22.759487 -20.631060 -27.453333  
3     -13.456365 -23.422222 -24.238613  
4     -28.828274 -29.621050 -29.809731  
...          ...        ...        ...  
34652  -1.203933  -1.300072   4.239341  
34653  -4.119704   0.074325  -2.552654  
34654   2.431003   1.558359   6.484763  
34655  -2.796966   1.794255   1.827837  
34656   0.832393   2.624338   4.115582  

[34657 rows x 289 columns]

In [ ]:
column_to_multiply = forecast.columns[1::]

constant = 0.002517

forecast[column_to_multiply] = forecast[column_to_multiply].multiply(constant)
forecast

WARNING - (py.warnings._showwarnmsg) - <ipython-input-167-39eb75a915d8>:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy




A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy




ds     step0     step1     step2     step3     step4  \
0     2023-01-02 00:00:00  0.008654 -0.027854 -0.025135 -0.024283 -0.032139   
1     2023-01-02 00:15:00 -0.020960 -0.018158 -0.012542 -0.033812 -0.042893   
2     2023-01-02 00:30:00 -0.011974 -0.007530 -0.029156 -0.036294 -0.050779   
3     2023-01-02 00:45:00  0.018307 -0.010383 -0.020933 -0.060722 -0.044689   
4     2023-01-02 01:00:00 -0.030426 -0.033087 -0.067792 -0.041665 -0.021155   
...                   ...       ...       ...       ...       ...       ...   
34652 2023-12-28 23:00:00  0.019729 -0.001941  0.008035  0.004626  0.015605   
34653 2023-12-28 23:15:00 -0.013398  0.011453  0.006003  0.001399 -0.007239   
34654 2023-12-28 23:30:00  0.030844  0.006987  0.006150 -0.008700  0.006301   
34655 2023-12-28 23:45:00 -0.007601  0.006512 -0.008812 -0.008249 -0.004679   
34656 2023-12-29 00:00:00  0.015382 -0.009693 -0.005876 -0.007408 -0.000723   

          step5     step6     step7     step8  ...   step278   step279  \
0     -0.060707 -0.070138 -0.044189 -0.040034  ... -0.071029 -0.068240   
1     -0.056263 -0.041215 -0.041948 -0.027705  ... -0.060914 -0.037689   
2     -0.055038 -0.035826 -0.025971 -0.040852  ... -0.044995 -0.068163   
3     -0.023556 -0.027724 -0.023304 -0.018204  ... -0.068458 -0.058277   
4     -0.032658 -0.018942 -0.034164 -0.041045  ... -0.053326 -0.058255   
...         ...       ...       ...       ...  ...       ...       ...   
34652 -0.009843  0.011203  0.001595 -0.007448  ... -0.004345  0.009177   
34653  0.009537 -0.013762 -0.008275 -0.007067  ...  0.009063 -0.009500   
34654 -0.013875  0.010127  0.001738 -0.018332  ... -0.009950  0.000928   
34655  0.006968 -0.013465 -0.030025 -0.016624  ...  0.004753 -0.010269   
34656 -0.021404 -0.022948 -0.006557 -0.006650  ... -0.018098 -0.018737   

        step280   step281   step282   step283   step284   step285   step286  \
0     -0.062180 -0.055977 -0.073821 -0.044627 -0.058512 -0.043297 -0.046329   
1     -0.050065 -0.065451 -0.045538 -0.051356 -0.033800 -0.038766 -0.034336   
2     -0.064581 -0.046846 -0.048907 -0.051659 -0.054618 -0.057286 -0.051928   
3     -0.061141 -0.056496 -0.052147 -0.034721 -0.039606 -0.033870 -0.058954   
4     -0.042228 -0.039312 -0.043193 -0.058699 -0.045707 -0.072561 -0.074556   
...         ...       ...       ...       ...       ...       ...       ...   
34652  0.004413 -0.008977  0.002631 -0.008002  0.008426 -0.003030 -0.003272   
34653 -0.003217 -0.002239 -0.017220 -0.007063 -0.008440 -0.010369  0.000187   
34654 -0.020394 -0.013905  0.002123  0.008925 -0.000873  0.006119  0.003922   
34655 -0.000908  0.003565  0.002201 -0.017745  0.000601 -0.007040  0.004516   
34656 -0.013407 -0.004689 -0.010574  0.008258 -0.006011  0.002095  0.006605   

        step287  
0     -0.035994  
1     -0.038760  
2     -0.069100  
3     -0.061009  
4     -0.075031  
...         ...  
34652  0.010670  
34653 -0.006425  
34654  0.016322  
34655  0.004601  
34656  0.010359  

[34657 rows x 289 columns]

In [ ]:
# forecast.to_csv('pv_Dayahead_20230102_20231228.csv',index=False)